In [11]:
import os
import pickle
import random
import time

import PIL
import numpy as np
import pandas as pd
import tensorflow as tf
from PIL import Image
from tensorflow.keras import Input, Model
from tensorflow.keras import backend as K
from tensorflow.keras.callbacks import TensorBoard
from tensorflow.keras.layers import Dense, LeakyReLU, BatchNormalization, ReLU, Reshape, UpSampling2D, Conv2D, Activation, \
    concatenate, Flatten, Lambda, Concatenate
from tensorflow.keras.optimizers import Adam
from matplotlib import pyplot as plt


import tensorflow as tf
    
with tf.device('/gpu:0'):
    def load_class_ids(class_info_file_path):
        """
        Load class ids from class_info.pickle file
        """
        with open(class_info_file_path, 'rb') as f:
            class_ids = pickle.load(f, encoding='latin1')
            return class_ids


    def load_embeddings(embeddings_file_path):
        """
        훈련된 텍스트 임베딩을 불러옴
        """
        with open(embeddings_file_path, 'rb') as f:
            embeddings = pickle.load(f, encoding='latin1')
            embeddings = np.array(embeddings)
            print('embeddings: ', embeddings.shape)
        return embeddings

    def load_filenames(filenames_file_path):
        """
        Load filenames.pickle file and return a list of all file names
        """
        with open(filenames_file_path, 'rb') as f:
            filenames = pickle.load(f, encoding='latin1')
        return filenames

    def load_bounding_boxes(dataset_dir):
        """
        이미지와 그에 상응하는 바운딩 박스를 짝지어 딕셔너리로 만들어 출력
        """
        # 바운딩 박스 전체 경로
        bounding_boxes_path = os.path.join(dataset_dir, 'list_bbox_celeba_pure.csv')
        file_paths_path = os.path.join(dataset_dir, 'list_filenames.csv')

        # bounding_boxes.txt 와 images.txt 파일을 읽어옴
        df_bounding_boxes = pd.read_csv(bounding_boxes_path, header=None).astype(int)
        df_file_names = pd.read_csv(file_paths_path, header=None)

        # 전체 이미지 파일 명이 순서대로 적힌 리스트를 만듬
        file_names = df_file_names[0].tolist() 

        # 파일 이름에 대응하는 바운딩 박스가 들어갈 딕셔너리를 만듬 (딕셔너리는 크기를 임의로 증가시킬수 있으므로 초기 사이즈는 아무렇게나)
        filename_boundingbox_dict = {}

        # 이미지 파일과 그에 해당하는 바운딩 박스를 딕셔너리로 만듬 (key = 이미지 파일 이름)
        for i in range(0, len(file_names)):
            # Get the bounding box
            bounding_box = df_bounding_boxes.iloc[i][:].tolist()
            key = file_names[i][:-4] + '.jpg'
            filename_boundingbox_dict[key] = bounding_box

        return filename_boundingbox_dict
    '''
    새 이미지가 크롭핑 되어있지 않기 크롭하기 위한 바운딩 박스 좌표 값이 파일에 주어지며,
    그 파일을 토대로 이미지를 크로핑 한 후,
    크로핑된 모든 이미지를 지정한 이미지 크기 (image_size) 값으로 바꾼다
    '''
    def get_img(img_path, bbox, image_size):
        """
        Load and resize image
        """
        img = Image.open(img_path).convert('RGB')
        width, height = img.size
        if bbox is not None:
            R = int(np.maximum(bbox[2], bbox[3]) * 0.75)
            center_x = int((2 * bbox[0] + bbox[2]) / 2)
            center_y = int((2 * bbox[1] + bbox[3]) / 2)
            y1 = np.maximum(0, center_y - R)
            y2 = np.minimum(height, center_y + R)
            x1 = np.maximum(0, center_x - R)
            x2 = np.minimum(width, center_x + R)
            img = img.crop([x1, y1, x2, y2])
        img = img.resize(image_size, PIL.Image.BILINEAR)
        return img


    def load_dataset(filenames_file_path, cub_dataset_dir, embeddings_file_path, image_size):
        """
        Load dataset
        """
        filenames = load_filenames(filenames_file_path)
        '''
        class_ids = load_class_ids(class_info_file_path)
        '''
        bounding_boxes = load_bounding_boxes(cub_dataset_dir)
        all_embeddings = load_embeddings(embeddings_file_path)

        X, y, embeddings = [], [], []

        print("Embeddings shape:", all_embeddings.shape)

        # 각 이미지에 해당하는 바운딩 박스 딕셔너리를 추출하여 get_img 함수로 크로핑되고 같은 크기로 바뀐 이미지를 
        for index, filename in enumerate(filenames):
            bounding_box = bounding_boxes[filename]

            try:
                # Load images
                img_name = '{0}/images/{1}'.format(cub_dataset_dir, filename)
                img = get_img(img_name, bounding_box, image_size)
                '''
                all_embeddings1 = all_embeddings[index, :, :]

                embedding_ix = random.randint(0, all_embeddings1.shape[0] - 1)
                '''
                embedding = all_embeddings[index, :]
                # X = 정제한 이미지 리스트
                X.append(np.array(img))
                '''
                # y = 정제한 이미지 인덱스
                y.append(class_ids[index])
                '''
                # embeddings = 
                embeddings.append(embedding)
            except Exception as e:
                print(e)

        X = np.array(X)
        y = np.array(y)
        embeddings = np.array(embeddings)
        return X, embeddings


    def generate_c(x):
        mean = x[:, :128]
        log_sigma = x[:, 128:]
        stddev = K.exp(log_sigma)
        epsilon = K.random_normal(shape=K.constant((mean.shape[1],), dtype='int32'))
        c = stddev * epsilon + mean
        return c


    def build_ca_model():
        """
        (1024,)의 텍스트 인코더 신경망의 출력을 입력으로 받고 (256,) 의 텐서를 출력
        """
        input_layer = Input(shape=(1024,))
        x = Dense(256)(input_layer)
        x = LeakyReLU(alpha=0.2)(x)
        model = Model(inputs=[input_layer], outputs=[x])
        return model


    def build_embedding_compressor_model():
        """
        입력 속성값 (40,) 을 (128,) 의 벡터로 확장하는 네트워크
        """
        input_layer = Input(shape=(40,))
        x = Dense(128)(input_layer)
        x = ReLU()(x)

        model = Model(inputs=[input_layer], outputs=[x])
        return model


    def build_stage1_generator():
        """
        Stage-I 의 generator 
        *** 이 신경망 안에 CA 신경망과 생성기 신경망이 들어가 있다!!!! ***
        그러므로, 입력으로 텍스트 임베딩 출력 (1024,)과 잡음 변수(100,) 을 받는다
        """
        '''
        input_layer = Input(shape=(1024,))
        x = Dense(256)(input_layer)
        mean_logsigma = LeakyReLU(alpha=0.2)(x)

        c = Lambda(generate_c)(mean_logsigma)

        input_layer2 = Input(shape=(100,))
        gen_input = Concatenate(axis=1)([c, input_layer2])
        '''
        # 텍스트 조건부 변수를 잡음 변수와 접합(concatenation) -> cGAN

        input_layer = Input(shape=(40,))
        x = Dense(128 * 8 * 4 * 4, use_bias=False)(input_layer)
        x = ReLU()(x)

        x = Reshape((4, 4, 128 * 8), input_shape=(128 * 8 * 4 * 4,))(x)

        x = UpSampling2D(size=(2, 2))(x)
        x = Conv2D(512, kernel_size=3, padding="same", strides=1, use_bias=False)(x)
        x = BatchNormalization()(x)
        x = ReLU()(x)

        x = UpSampling2D(size=(2, 2))(x)
        x = Conv2D(256, kernel_size=3, padding="same", strides=1, use_bias=False)(x)
        x = BatchNormalization()(x)
        x = ReLU()(x)

        x = UpSampling2D(size=(2, 2))(x)
        x = Conv2D(128, kernel_size=3, padding="same", strides=1, use_bias=False)(x)
        x = BatchNormalization()(x)
        x = ReLU()(x)

        x = UpSampling2D(size=(2, 2))(x)
        x = Conv2D(64, kernel_size=3, padding="same", strides=1, use_bias=False)(x)
        x = BatchNormalization()(x)
        x = ReLU()(x)

        x = Conv2D(3, kernel_size=3, padding="same", strides=1, use_bias=False)(x)
        x = Activation(activation='tanh')(x)

        stage1_gen = Model(inputs=input_layer, outputs=x)
        '''
        stage - I gen 은 입력된 문장의 임베딩을 바탕으로 (+잡음 변수) 이미지를 생성 함 
        '''
        return stage1_gen


    def build_stage1_discriminator():
        """
        Create a model which takes two inputs
        1. One from above network
        2. One from the embedding layer
        3. Concatenate along the axis dimension and feed it to the last module which produces final logits
        """
        input_layer = Input(shape=(64, 64, 3))

        x = Conv2D(64, (4, 4),
                   padding='same', strides=2,
                   input_shape=(64, 64, 3), use_bias=False)(input_layer)
        x = LeakyReLU(alpha=0.2)(x)

        x = Conv2D(128, (4, 4), padding='same', strides=2, use_bias=False)(x)
        x = BatchNormalization()(x)
        x = LeakyReLU(alpha=0.2)(x)

        x = Conv2D(256, (4, 4), padding='same', strides=2, use_bias=False)(x)
        x = BatchNormalization()(x)
        x = LeakyReLU(alpha=0.2)(x)

        x = Conv2D(512, (4, 4), padding='same', strides=2, use_bias=False)(x)
        x = BatchNormalization()(x)
        x = LeakyReLU(alpha=0.2)(x)

        '''
        실제 이미지에 해당하는 압축된 임베딩을 입력
        '''
        input_layer2 = Input(shape=(4, 4, 128))

        '''
        입력 이미지와 압축 텍스트 임베딩을 합침
        '''
        merged_input = concatenate([x, input_layer2])

        x2 = Conv2D(64 * 8, kernel_size=1,
                    padding="same", strides=1)(merged_input)
        x2 = BatchNormalization()(x2)
        x2 = LeakyReLU(alpha=0.2)(x2)
        x2 = Flatten()(x2)
        x2 = Dense(1)(x2)
        x2 = Activation('sigmoid')(x2)

        stage1_dis = Model(inputs=[input_layer, input_layer2], outputs=x2)
        '''
        출력은 입력 이미지가 진짜인지 가짜인지에 관한 확률(sigmoid)을 출력
        '''
        return stage1_dis


    def build_adversarial_model(gen_model, dis_model):
        input_layer = Input(shape=(40,))
        input_layer3 = Input(shape=(4, 4, 128))

        x = gen_model(input_layer)

        dis_model.trainable = False
        valid = dis_model([x, input_layer3])

        model = Model(inputs=[input_layer, input_layer3], outputs=valid)
        return model


    def KL_loss(y_true, y_pred):
        mean = y_pred[:, :128]
        logsigma = y_pred[:, :128]
        loss = -logsigma + .5 * (-1 + K.exp(2. * logsigma) + K.square(mean))
        loss = K.mean(loss)
        return loss


    def custom_generator_loss(y_true, y_pred):
        # Calculate binary cross entropy loss
        return K.binary_crossentropy(y_true, y_pred)


    def save_rgb_img(img, path):
        """
        Save an rgb image
        """
        fig = plt.figure()
        ax = fig.add_subplot(1, 1, 1)
        ax.imshow(img)
        ax.axis("off")
        ax.set_title("Image")

        plt.savefig(path)
        plt.close()


    def write_log(callback, name, loss, batch_no):
        """
        Write training summary to TensorBoard
        """
        with callback.as_default():
              tf.summary.scalar(name, loss, batch_no)
              callback.flush()
 







    '''
    Stage - I stackGAN 훈련
    '''
    if __name__ == '__main__':
        '''
        하이퍼파라미터(불변 파라미터) 지정
        '''
        data_dir = "C:/Users/user/Desktop/CelebA_dataset_reduce"
        train_dir = data_dir + "/train"
        test_dir = data_dir + "/test"
        image_size = 64
        batch_size = 100
        z_dim = 100
        stage1_generator_lr = 0.0002
        stage1_discriminator_lr = 0.0002
        stage1_lr_decay_step = 600
        epochs = 500
        condition_dim = 128

        embeddings_file_path_train = train_dir + "/attr_(embeddings).pickle"
        embeddings_file_path_test = test_dir + "/attr_(embeddings).pickle"

        filenames_file_path_train = train_dir + "/filenames.pickle"
        filenames_file_path_test = test_dir + "/filenames.pickle"

        '''
        class_info_file_path_train = train_dir + "/class_info.pickle"
        class_info_file_path_test = test_dir + "/class_info.pickle"
        '''

        cub_dataset_dir = data_dir + "/img_align_celeba"

        '''
        optimizer 정의
        '''
        dis_optimizer = Adam(lr=stage1_discriminator_lr, beta_1=0.5, beta_2=0.999)
        gen_optimizer = Adam(lr=stage1_generator_lr, beta_1=0.5, beta_2=0.999)

        """"
        dataset 로드하기
        """
        X_train, embeddings_train = load_dataset(filenames_file_path=filenames_file_path_train,
                                                          cub_dataset_dir=cub_dataset_dir,
                                                          embeddings_file_path=embeddings_file_path_train,
                                                          image_size=(64, 64))

        X_test, embeddings_test = load_dataset(filenames_file_path=filenames_file_path_test,
                                                       cub_dataset_dir=cub_dataset_dir,
                                                       embeddings_file_path=embeddings_file_path_test,
                                                       image_size=(64, 64))

       

embeddings:  (16000, 40)
Embeddings shape: (16000, 40)
embeddings:  (4000, 40)
Embeddings shape: (4000, 40)


In [12]:
with tf.device('/gpu:0'):
        """
        신경망 빌드 & compile
        """
        '''
        ca_model = build_ca_model()
        ca_model.compile(loss="binary_crossentropy", optimizer="adam")
        '''
        stage1_dis = build_stage1_discriminator()
        stage1_dis.compile(loss='binary_crossentropy', optimizer=dis_optimizer)

        stage1_gen = build_stage1_generator()
        stage1_gen.compile(loss="mse", optimizer=gen_optimizer)

        embedding_compressor_model = build_embedding_compressor_model()
        embedding_compressor_model.compile(loss="binary_crossentropy", optimizer="adam")

        '''
        stage-I GAN 빌드& 컴파일
        이때, stage-I 의 discriminator 는 훈련시키지 않고 stage-I generator 의 가중치만 업데이트
        '''
        adversarial_model = build_adversarial_model(gen_model=stage1_gen, dis_model=stage1_dis)
        adversarial_model.compile(loss=['binary_crossentropy', KL_loss], loss_weights=[1, 2.0],
                                  optimizer=gen_optimizer, metrics=None)

        tensorboard = tf.summary.create_file_writer("logs/".format(time.time()))
        """
        tensorboard.set_model(stage1_gen)
        tensorboard.set_model(stage1_dis)
        '''
        tensorboard.set_model(ca_model)
        '''
        tensorboard.set_model(embedding_compressor_model)
        """
        # Generate an array containing real and fake values
        # Apply label smoothing as well
        real_labels = np.ones((batch_size, 1), dtype=float) * 0.9
        fake_labels = np.zeros((batch_size, 1), dtype=float) * 0.1
        '''
        매 epoch 마다 아래를 반복함
        '''
        for epoch in range(epochs):
            print("========================================")
            print("Epoch is:", epoch)
            print("Number of batches", int(X_train.shape[0] / batch_size))

            gen_losses = []
            dis_losses = []

            # Load data and train model
            number_of_batches = int(X_train.shape[0] / batch_size)
            for index in range(number_of_batches):
                print("Batch:{}".format(index+1))
                '''
                모델에 입력으로 들어갈 이미지와 텍스트 임베딩을 받아옴 (각 텍스트 임베딩은 각 이미지에 대응 됨)
                '''
                # 원래는 CA 의 출력이 stage-I 으로 들어가야 하지만 gen 안에 CA 가 있음
                z_noise = np.random.normal(0, 1, size=(batch_size, z_dim))
                # 배치 사이즈만큼 훈련(실제) 이미지를 추출
                image_batch = X_train[index * batch_size:(index + 1) * batch_size]
                # 추출한 이미지에 대응하는 임베딩을 추출
                embedding_batch = embeddings_train[index * batch_size:(index + 1) * batch_size]
                # 이미지들을 정규화하여 값을 작게 만듬
                image_batch = (image_batch - 127.5) / 127.5

                # stage-I 의 gen 에서 텍스트 임베딩을 바탕으로 저 해상도 fake 이미지를 생성
                # 이때, 두 stage 는 랜덤하게 생성한 텍스트 임베딩을 나머지 입력으로 받음
                fake_images = stage1_gen.predict(embedding_batch, verbose=3)

                # stage-I dis 에 들어갈 압축 텍스트 임베딩을 랜덤하게 생성한 텍스트 임베딩 기반으로 생성
                compressed_embedding = embedding_compressor_model.predict_on_batch(embedding_batch)
                compressed_embedding = np.reshape(compressed_embedding, (-1, 1, 1, condition_dim))
                compressed_embedding = np.tile(compressed_embedding, (1, 4, 4, 1))
                '''
                discriminator 에서 입력 이미지가 CNN 을 통과한 결과와 속성값 (40,) 을 concatenate 해 주기 위해서는,
                속성값 (40,) 를 compressor 네트워크를 통해 (128,) 로 확장하고,
                reshape, tile 함수를 이용해 CNN 결과 (4, 4, 512) 와 (4, 4, :) 부분을 맞추어 주어야 한다.
                '''
                
                """
                stage-I dis 를 훈련함
                """
                # 실제 이미지와 압축 텍스트 임베딩을 입력으로 하고 모든 레이블을 1 (이미지가 진짜라는 의미) 로 하여,
                # dis 가 실제 이미지를 잘 분류 하게끔 훈련
                dis_loss_real = stage1_dis.train_on_batch([image_batch, compressed_embedding],
                                                          np.reshape(real_labels, (batch_size, 1)))
                # gen 이 생성한 가짜 이미지와 압축 텍스트 임베딩을 입력으로 하고 모든 레이블을 0 (이미지가 가짜라는 의미) 로 하여,
                # dis 가 가짜 이미지를 잘 분류 하게끔 훈련
                dis_loss_fake = stage1_dis.train_on_batch([fake_images, compressed_embedding],
                                                          np.reshape(fake_labels, (batch_size, 1)))
                # 실제 이미지와 압축 텍스트 임베딩을 입력으로 하고 모든 레이블을 0 (이미지가 가짜라는 의미) 로 하여,
                # dis 가 실제 이미지를 잘 분류 하게끔 훈련
                dis_loss_wrong = stage1_dis.train_on_batch([image_batch[:(batch_size - 1)], compressed_embedding[1:]],
                                                           np.reshape(fake_labels[1:], (batch_size-1, 1)))

                d_loss = 0.5 * np.add(dis_loss_real, 0.5 * np.add(dis_loss_wrong, dis_loss_fake))

                print("d_loss_real:{}".format(dis_loss_real))
                print("d_loss_fake:{}".format(dis_loss_fake))
                print("d_loss_wrong:{}".format(dis_loss_wrong))
                print("d_loss:{}".format(d_loss))

                """
                stage-I GAN 을 훈련함
                이때, stage-I 의 discriminator 는 훈련시키지 않고 stage-I generator 의 가중치만 업데이트
                """
                g_loss = adversarial_model.train_on_batch([embedding_batch, compressed_embedding],[K.ones((batch_size, 1)) * 0.9, K.ones((batch_size, 256)) * 0.9])
                print("g_loss:{}".format(g_loss))

                dis_losses.append(d_loss)
                gen_losses.append(g_loss)

            """
            각 epoch 마다 Tensorboard 에 loss 저장
            """
            
            write_log(tensorboard, 'discriminator_loss', np.mean(dis_losses), epoch)
            write_log(tensorboard, 'generator_loss', np.mean(gen_losses[0]), epoch)
            '''
            tf.summary.scalar('discriminator_loss', np.mean(dis_losses), epoch)
            tf.summary.scalar('generator_loss', np.mean(gen_losses[0]), epoch)
            
            tf.summary.scalar('discriminator_loss', np.mean(dis_losses))
            tf.summary.scalar('generator_loss', np.mean(gen_losses[0]))
            summary_op = tf.summary.merge()
            summary_writer = tf.summary.FileWriter("logs/".format(time.time()))
            '''    
            # 매 두번의 epoch 마다 이미지 gen & 이미지 저장
            if epoch % 2 == 0:
                # z_noise2 = np.random.uniform(-1, 1, size=(batch_size, z_dim))
                z_noise2 = np.random.normal(0, 1, size=(batch_size, z_dim))
                embedding_batch = embeddings_test[0:batch_size]
                fake_images = stage1_gen.predict_on_batch(embedding_batch)

                # Save images
                for i, img in enumerate(fake_images[:10]):
                    save_rgb_img(img, "results/gen_{}_{}.png".format(epoch, i))
                    
            if epoch % 50 == 0:
                # Save models
                stage1_gen.save_weights("weights/stage1_gen_epoch_{0}.h5".format(epochs))
                stage1_dis.save_weights("weights/stage1_dis_epoch_{0}.h5".format(epochs))

        '''
        이제 훈련된 stage-I 의 generator 와 discriminator 을 얻음 (+ embedding_compressor) 
        '''

Epoch is: 0
Number of batches 160
Batch:1
d_loss_real:0.9524253010749817
d_loss_fake:2.5623180866241455
d_loss_wrong:6.464722156524658
d_loss:2.7329727113246918
g_loss:0.7495062947273254
Batch:2
d_loss_real:0.708916187286377
d_loss_fake:2.7132070064544678
d_loss_wrong:0.27398914098739624
d_loss:1.1012571305036545
g_loss:0.8303829431533813
Batch:3
d_loss_real:3.1680121421813965
d_loss_fake:0.006696307100355625
d_loss_wrong:1.129776954650879
d_loss:1.8681243865285069
g_loss:0.7853962779045105
Batch:4
d_loss_real:1.7963413000106812
d_loss_fake:1.5281389951705933
d_loss_wrong:0.7303647398948669
d_loss:1.4627965837717056
g_loss:0.8928167819976807
Batch:5
d_loss_real:2.1988766193389893
d_loss_fake:0.0010505211539566517
d_loss_wrong:1.1646205186843872
d_loss:1.3908560696290806
g_loss:0.7692187428474426
Batch:6
d_loss_real:1.7459869384765625
d_loss_fake:0.8242931365966797
d_loss_wrong:0.6030779480934143
d_loss:1.2298362404108047
g_loss:0.8898969888687134
Batch:7
d_loss_real:1.9829972982406616


g_loss:0.32867327332496643
Batch:53
d_loss_real:0.9712552428245544
d_loss_fake:0.0011833091266453266
d_loss_wrong:0.7469258904457092
d_loss:0.6726549213053659
g_loss:0.3252657651901245
Batch:54
d_loss_real:0.9267425537109375
d_loss_fake:0.0013657803647220135
d_loss_wrong:0.8007151484489441
d_loss:0.6638915090588853
g_loss:0.32554706931114197
Batch:55
d_loss_real:0.9041599035263062
d_loss_fake:0.001292056986130774
d_loss_wrong:0.7493239641189575
d_loss:0.6397339570394251
g_loss:0.32536181807518005
Batch:56
d_loss_real:0.9280430674552917
d_loss_fake:0.001167134614661336
d_loss_wrong:0.7669690251350403
d_loss:0.6560555736650713
g_loss:0.32532066106796265
Batch:57
d_loss_real:1.0170832872390747
d_loss_fake:0.0011413013562560081
d_loss_wrong:0.7304767370223999
d_loss:0.6914461532142013
g_loss:0.3256334364414215
Batch:58
d_loss_real:0.9264374375343323
d_loss_fake:0.0010753399692475796
d_loss_wrong:0.7471488118171692
d_loss:0.6502747567137703
g_loss:0.32632896304130554
Batch:59
d_loss_real:0.

g_loss:0.32521143555641174
Batch:105
d_loss_real:0.890494704246521
d_loss_fake:0.0011520246043801308
d_loss_wrong:0.7023113369941711
d_loss:0.6211131925228983
g_loss:0.3257254362106323
Batch:106
d_loss_real:0.8831196427345276
d_loss_fake:0.0008842262905091047
d_loss_wrong:0.7188153266906738
d_loss:0.6214847096125595
g_loss:0.32604876160621643
Batch:107
d_loss_real:0.8738458752632141
d_loss_fake:0.0007980641676113009
d_loss_wrong:0.7101934552192688
d_loss:0.6146708174783271
g_loss:0.326974093914032
Batch:108
d_loss_real:0.8948071002960205
d_loss_fake:0.000906518311239779
d_loss_wrong:0.6780251264572144
d_loss:0.6171364613401238
g_loss:0.32786327600479126
Batch:109
d_loss_real:0.9296126365661621
d_loss_fake:0.0009363933932036161
d_loss_wrong:0.7181339263916016
d_loss:0.6445738982292823
g_loss:0.3253423273563385
Batch:110
d_loss_real:0.8610684871673584
d_loss_fake:0.0008852175087668002
d_loss_wrong:0.719615638256073
d_loss:0.6106594575248891
g_loss:0.32911741733551025
Batch:111
d_loss_rea

g_loss:0.3287770450115204
Batch:157
d_loss_real:0.8961966633796692
d_loss_fake:0.0009079077281057835
d_loss_wrong:0.6796181201934814
d_loss:0.6182298386702314
g_loss:0.3266826570034027
Batch:158
d_loss_real:0.9044119119644165
d_loss_fake:0.0010528065031394362
d_loss_wrong:0.6667245626449585
d_loss:0.6191502982692327
g_loss:0.3280336260795593
Batch:159
d_loss_real:0.8307336568832397
d_loss_fake:0.0010847668163478374
d_loss_wrong:0.7040585875511169
d_loss:0.5916526670334861
g_loss:0.33073967695236206
Batch:160
d_loss_real:0.8229233622550964
d_loss_fake:0.001044617616571486
d_loss_wrong:0.7300274968147278
d_loss:0.594229709735373
g_loss:0.3314770460128784


Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping i

...

Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).


Epoch is: 211
Number of batches 160
Batch:1
d_loss_real:0.32987359166145325
d_loss_fake:1.9705114482349018e-06
d_loss_wrong:0.0005315175512805581
d_loss:0.16507016784640882
g_loss:0.3254269063472748
Batch:2
d_loss_real:0.32563912868499756
d_loss_fake:1.554880327603314e-06
d_loss_wrong:0.0006999601610004902
d_loss:0.1629949431028308
g_loss:0.3251820504665375
Batch:3
d_loss_real:0.32630717754364014
d_loss_fake:1.6544264553886023e-06
d_loss_wrong:0.0020138402469456196
d_loss:0.16365746244017032
g_loss:0.3254139721393585
Batch:4
d_loss_real:0.32812079787254333
d_loss_fake:1.5451087165274657e-06
d_loss_wrong:0.0011828031856566668
d_loss:0.16435648600986497
g_loss:0.32527512311935425
Batch:5
d_loss_real:0.3263128697872162
d_loss_fake:1.2575177379403613e-06
d_loss_wrong:0.00023056745703797787
d_loss:0.16321439113730207
g_loss:0.3255946636199951
Batch:6
d_loss_real:0.3626982569694519
d_loss_fake:2.3756733753543813e-06
d_loss_wrong:0.0002646516659297049
d_loss:0.18141588531955222
g_loss:0.32850

d_loss_real:0.32597115635871887
d_loss_fake:3.698930186146754e-06
d_loss_wrong:0.00035467048292048275
d_loss:0.1630751705326361
g_loss:0.3254319131374359
Batch:52
d_loss_real:0.32591673731803894
d_loss_fake:3.8383104765671305e-06
d_loss_wrong:0.0008009234443306923
d_loss:0.16315955909772129
g_loss:0.32532817125320435
Batch:53
d_loss_real:0.3296264410018921
d_loss_fake:2.98153463518247e-06
d_loss_wrong:0.001084408606402576
d_loss:0.16508506803620548
g_loss:0.3258715867996216
Batch:54
d_loss_real:0.3279522955417633
d_loss_fake:2.622685769892996e-06
d_loss_wrong:0.0028266259469091892
d_loss:0.16468345992905142
g_loss:0.3251502215862274
Batch:55
d_loss_real:0.3265289068222046
d_loss_fake:3.6661356261902256e-06
d_loss_wrong:0.0005834621842950583
d_loss:0.1634112354910826
g_loss:0.32541775703430176
Batch:56
d_loss_real:0.32844439148902893
d_loss_fake:3.5798368571704486e-06
d_loss_wrong:0.001234635361470282
d_loss:0.16453174954409633
g_loss:0.32535529136657715
Batch:57
d_loss_real:0.349134832

g_loss:0.32522401213645935
Batch:102
d_loss_real:0.32951533794403076
d_loss_fake:4.119694494875148e-06
d_loss_wrong:0.0006339264218695462
d_loss:0.1649171805011065
g_loss:0.32524561882019043
Batch:103
d_loss_real:0.3267323672771454
d_loss_fake:3.7417180465126876e-06
d_loss_wrong:0.0006910379743203521
d_loss:0.1635398785616644
g_loss:0.3254110813140869
Batch:104
d_loss_real:0.3264661133289337
d_loss_fake:3.952575752919074e-06
d_loss_wrong:8.50293945404701e-05
d_loss:0.1632553021570402
g_loss:0.32532164454460144
Batch:105
d_loss_real:0.3386218547821045
d_loss_fake:5.64766742172651e-06
d_loss_wrong:6.484576442744583e-05
d_loss:0.16932855074901454
g_loss:0.32986971735954285
Batch:106
d_loss_real:0.3390798568725586
d_loss_fake:4.332158823672216e-06
d_loss_wrong:0.00016262759163510054
d_loss:0.169581668373894
g_loss:0.325452983379364
Batch:107
d_loss_real:0.3257722556591034
d_loss_fake:3.841989837383153e-06
d_loss_wrong:0.0014461670070886612
d_loss:0.1632486300787832
g_loss:0.325613290071487

KeyboardInterrupt: 